In [1]:
import pandas as pd
import numpy as np
import os
from util import HISTORICAL_FILE_JOIN, RESOURCE_DIR 
#pip install mlxtend
from mlxtend.frequent_patterns import apriori, association_rules

 Generates association rules for the results found in the projects history last slice.

In [2]:
#df = pd.read_excel("historical_join.xlsx", keep_default_na=False)
df = pd.read_excel(HISTORICAL_FILE_JOIN, keep_default_na=False)

len(df)
df.head()

owner      name                        domain  \
0  Activiti  Activiti  Enterprise Resource Planning   
1  Activiti  Activiti  Enterprise Resource Planning   
2  Activiti  Activiti  Enterprise Resource Planning   
3  Activiti  Activiti  Enterprise Resource Planning   
4  Activiti  Activiti  Enterprise Resource Planning   

                                       sha1  part_commit  \
0  7262dc3913045001cbc658a8474e9d295980c345            1   
1  38b284602be9dcb6b4253cfa1c2f9420c002b56a            2   
2  fbcdc18a66e7f7960a7ed966f87b1527c5c7551a            3   
3  8d05dda18ce4c5db6f30cf01d7e0c2059b1a5388            4   
4  a789ba2b30383777b4d0d81bbc62a90a24dbb032            5   

                 date_commit  isLast  SapHana  Realm  SAP SQL Anywhere  ...  \
0  2010-07-14 06:36:18+00:00   False        0      0                 0  ...   
1  2010-08-03 08:31:19+00:00   False        0      0                 0  ...   
2  2010-09-02 09:45:24+00:00   False        0      0                 0  ...   
3  2010-09-16 15:33:33+00:00   False        0      0                 0  ...   
4  2010-09-23 13:38:28+00:00   False        0      0                 0  ...   

   Firebird  Cassandra  Couchbase  Etcd  PostGIS  Redis  Join_Ignite-Sql  \
0         0          0          0     0        0      0                0   
1         0          0          0     0        0      0                0   
2         0          0          0     0        0      0                0   
3         0          0          0     0        0      0                0   
4         0          0          0     0        0      0                0   

   Join_Ignite-NoSql  Join_Virtuoso-Sql  Join_Virtuoso-NoSql  
0                  0                  0                    0  
1                  0                  0                    0  
2                  0                  0                    0  
3                  0                  0                    0  
4                  0                  0                    0  

[5 rows x 57 columns]

In [3]:
df2 = df.copy()
df2

owner            name                        domain  \
0      Activiti        Activiti  Enterprise Resource Planning   
1      Activiti        Activiti  Enterprise Resource Planning   
2      Activiti        Activiti  Enterprise Resource Planning   
3      Activiti        Activiti  Enterprise Resource Planning   
4      Activiti        Activiti  Enterprise Resource Planning   
...         ...             ...                           ...   
31111   liferay  liferay-portal  Enterprise Resource Planning   
31112   liferay  liferay-portal  Enterprise Resource Planning   
31113   liferay  liferay-portal  Enterprise Resource Planning   
31114   liferay  liferay-portal  Enterprise Resource Planning   
31115   liferay  liferay-portal  Enterprise Resource Planning   

                                           sha1  part_commit  \
0      7262dc3913045001cbc658a8474e9d295980c345            1   
1      38b284602be9dcb6b4253cfa1c2f9420c002b56a            2   
2      fbcdc18a66e7f7960a7ed966f87b1527c5c7551a            3   
3      8d05dda18ce4c5db6f30cf01d7e0c2059b1a5388            4   
4      a789ba2b30383777b4d0d81bbc62a90a24dbb032            5   
...                                         ...          ...   
31111  fcd4cd6526c80613eca69927effe931bb6a91444         8209   
31112  cc0ab8103195e543056639c8c2883fcc187c33a2         8210   
31113  f75082029372ab28694650bd3fe9fae4d548351e         8211   
31114  a80a679a86d2867f985bafa510d9d12f1bf051a7         8212   
31115  94fc05263efbf1962540a71f90cc8ab36734ee51         8213   

                     date_commit  isLast  SapHana  Realm  SAP SQL Anywhere  \
0      2010-07-14 06:36:18+00:00   False        0      0                 0   
1      2010-08-03 08:31:19+00:00   False        0      0                 0   
2      2010-09-02 09:45:24+00:00   False        0      0                 0   
3      2010-09-16 15:33:33+00:00   False        0      0                 0   
4      2010-09-23 13:38:28+00:00   False        0      0                 0   
...                          ...     ...      ...    ...               ...   
31111  2024-10-07 12:05:23+00:00   False        0      0                 0   
31112  2024-10-07 17:58:58+00:00   False        0      0                 0   
31113  2024-10-11 04:36:52+00:00   False        0      0                 0   
31114  2024-10-11 16:53:22+00:00   False        0      0                 0   
31115  2024-10-14 12:55:58+00:00   False        0      0                 0   

       ...  Firebird  Cassandra  Couchbase  Etcd  PostGIS  Redis  \
0      ...         0          0          0     0        0      0   
1      ...         0          0          0     0        0      0   
2      ...         0          0          0     0        0      0   
3      ...         0          0          0     0        0      0   
4      ...         0          0          0     0        0      0   
...    ...       ...        ...        ...   ...      ...    ...   
31111  ...         0          0          0     0        1      1   
31112  ...         0          0          0     0        1      1   
31113  ...         0          0          0     0        1      1   
31114  ...         0          0          0     0        1      1   
31115  ...         0          0          0     0        1      1   

       Join_Ignite-Sql  Join_Ignite-NoSql  Join_Virtuoso-Sql  \
0                    0                  0                  0   
1                    0                  0                  0   
2                    0                  0                  0   
3                    0                  0                  0   
4                    0                  0                  0   
...                ...                ...                ...   
31111                0                  0                  0   
31112                0                  0                  0   
31113                0                  0                  0   
31114                0                  0                  0   
31

Grouping the lines to identify which projects that don't have DB clues

In [4]:
df2 = df.groupby(["owner", "name"]).sum()
df2

part_commit  isLast  SapHana  Realm  \
owner           name                                                      
Activiti        Activiti                   1540       0        0      0   
Alluxio         alluxio                    5886       0        0      0   
AlmasB          FXGL                        105       0        0      0   
AntennaPod      AntennaPod                  703       0        0      0   
AnySoftKeyboard AnySoftKeyboard             703       0        0      0   
...                                         ...     ...      ...    ...   
xuxueli         xxl-job                     120       0        0      0   
yacy            yacy_search_server         5151       0        0      0   
zaproxy         zaproxy                     666       0        0      0   
zendesk         maxwell                     105       0        0      0   
zxing           zxing                       666       0        0      0   

                                    SAP SQL Anywhere  FileMaker  ArangoDB  \
owner           name                                                        
Activiti        Activiti                           0          0         0   
Alluxio         alluxio                            0          0         0   
AlmasB          FXGL                               0          0         0   
AntennaPod      AntennaPod                         0          0         0   
AnySoftKeyboard AnySoftKeyboard                    0          0         0   
...                                              ...        ...       ...   
xuxueli         xxl-job                            0          0         0   
yacy            yacy_search_server                 0          0         0   
zaproxy         zaproxy                            0          0         0   
zendesk         maxwell                            0          0         0   
zxing           zxing                              0          0         0   

                                    Informix  HyperSQL  CouchDB  ...  \
owner           name                                             ...   
Activiti        Activiti                   0        13        0  ...   
Alluxio         alluxio                    0         0        0  ...   
AlmasB          FXGL                       0         0        0  ...   
AntennaPod      AntennaPod                 0         0        0  ...   
AnySoftKeyboard AnySoftKeyboard            0         0        0  ...   
...                                      ...       ...      ...  ...   
xuxueli         xxl-job                    0         0        0  ...   
yacy            yacy_search_server         0         0        0  ...   
zaproxy         zaproxy                    0        36        0  ...   
zendesk         maxwell                    0         0        0  ...   
zxing           zxing                      0         0        0  ...   

                                    Firebird  Cassandra  Couchbase  Etcd  \
owner           name                                                       
Activiti        Activiti                   0          0          0     0   
Alluxio         alluxio                    0          0          0     4   
AlmasB          FXGL                       0          0          0     0   
AntennaPod      AntennaPod                 0          0          0     0   
AnySoftKeyboard AnySoftKeyboard            0          0          0     0   
...                                      ...        ...        ...   ...   
xuxueli         xxl-job                    0          0          0     0   
yacy            yacy_search_server         0          0          0     0   
zaproxy         zaproxy                    0          0          0     0   
zendesk         maxwell                    0          0          0     0   
zxing           zxing                      0          0          0     0   

                                    PostGIS  Redis  Join_Ignite-Sql  \
owner           name                                         

Reseting the index column

In [5]:
df2 = df2.reset_index()
df2

owner                name  part_commit  isLast  SapHana  Realm  \
0           Activiti            Activiti         1540       0        0      0   
1            Alluxio             alluxio         5886       0        0      0   
2             AlmasB                FXGL          105       0        0      0   
3         AntennaPod          AntennaPod          703       0        0      0   
4    AnySoftKeyboard     AnySoftKeyboard          703       0        0      0   
..               ...                 ...          ...     ...      ...    ...   
357          xuxueli             xxl-job          120       0        0      0   
358             yacy  yacy_search_server         5151       0        0      0   
359          zaproxy             zaproxy          666       0        0      0   
360          zendesk             maxwell          105       0        0      0   
361            zxing               zxing          666       0        0      0   

     SAP SQL Anywhere  FileMaker  ArangoDB  Informix  ...  Firebird  \
0                   0          0         0         0  ...         0   
1                   0          0         0         0  ...         0   
2                   0          0         0         0  ...         0   
3                   0          0         0         0  ...         0   
4                   0          0         0         0  ...         0   
..                ...        ...       ...       ...  ...       ...   
357                 0          0         0         0  ...         0   
358                 0          0         0         0  ...         0   
359                 0          0         0         0  ...         0   
360                 0          0         0         0  ...         0   
361                 0          0         0         0  ...         0   

     Cassandra  Couchbase  Etcd  PostGIS  Redis  Join_Ignite-Sql  \
0            0          0     0        0      0                0   
1            0          0     4        0      0                0   
2            0          0     0        0      0                0   
3            0          0     0        0      0                0   
4            0          0     0        0      0                0   
..         ...        ...   ...      ...    ...              ...   
357          0          0     0        0      1                0   
358          0          0     0        0      0                0   
359          0          0     0        0      0                0   
360          0          0     0        0      7                0   
361          0          0     0        0      0                0   

     Join_Ignite-NoSql  Join_Virtuoso-Sql  Join_Virtuoso-NoSql  
0                    0                  0                    0  
1                    0                  0                    0  
2                    0                  0                    0  
3                    0                  0                    0  
4                    0                  0                    0  
..                 ...                ...                  ...  
357                  0                  0                    0  
358                  0                  0                    0  
359                  0                  0                    0  
360                  0                  0                    0  
361                  0                  0                    0  

[362 rows x 54 columns]

New dataframe filtering only lines that last version projects

In [6]:
#df10 = df2.mask(df2 > 1, 1)
#df10 = df[(df['COMMITS'] == 10)]
#df10

# Função para selecionar o último commit
def select_last_commit(group):
    return group.iloc[-1]  # Seleciona o último commit

# Ordena os commits dentro de cada projeto (caso não estejam ordenados)
df_sorted = df.sort_values(by=['name', 'part_commit'])

# Aplica a função para pegar o último commit em cada grupo de projeto
df10 = df_sorted.groupby('name').apply(select_last_commit).reset_index(drop=True)

df10


owner                           name  \
0           Activiti                       Activiti   
1    CellularPrivacy  Android-IMSI-Catcher-Detector   
2             Blankj                AndroidUtilCode   
3         AntennaPod                     AntennaPod   
4    AnySoftKeyboard                AnySoftKeyboard   
..               ...                            ...   
356           apache                       zeppelin   
357       openzipkin                         zipkin   
358           apache                      zookeeper   
359            zxing                          zxing   
360      journeyapps         zxing-android-embedded   

                           domain                                      sha1  \
0    Enterprise Resource Planning  1667609eb4fb666fd9245f86ee1d7864644732f5   
1                        Security  80d6446ea02d66836305d8ffcd6405a805d023ae   
2            Software Development  d1ff4e3cd680473dc63b491a9795bd790a464949   
3                           Media  dd8bf381c4012558778abbefc14c1741dbab43a3   
4                           Other  2fc649dc3398b1c762a85a803a43ce814519665b   
..                            ...                                       ...   
356               Data Management  c5ccc8e584934fa4f96de486cd97312180147b1f   
357                    Monitoring  2ada407cd88f5360b4180e1df33a4dea0421774a   
358     Infrastructure Management  6e746f8e881bfeb99cf0f74fa50a3d9c9d679229   
359          Software Development  fc2f1c9b0f0218c72ec5cab0d4030b4abfb73945   
360                       Network  e8257760da9c36c5f7b512b8dbc0c84ada20ad7c   

     part_commit                date_commit  isLast  SapHana  Realm  \
0             55  2024-02-14 12:26:10+00:00   False        0      0   
1             13  2024-08-15 21:37:58+00:00   False        0      1   
2             11  2020-10-24 19:52:23+00:00   False        0      0   
3             37  2024-05-18 17:26:39+00:00   False        0      0   
4             37  2024-03-15 16:31:10+00:00   False        0      0   
..           ...                        ...     ...      ...    ...   
356           43  2024-09-29 15:41:29+00:00   False        0      0   
357           26  2024-02-11 12:02:55+00:00   False        0      0   
358           25  2023-07-18 12:04:24+00:00   False        0      0   
359           36  2023-08-17 02:56:52+00:00   False        0      0   
360           10  2018-03-04 11:14:00+00:00   False        0      0   

     SAP SQL Anywhere  ...  Firebird  Cassandra  Couchbase  Etcd  PostGIS  \
0                   0  ...         0          0          0     0        0   
1                   0  ...         0          0          0     0        0   
2                   0  ...         0          0          0     0        0   
3                   0  ...         0          0          0     0        0   
4                   0  ...         0          0          0     0        0   
..                ...  ...       ...        ...        ...   ...      ...   
356                 0  ...         0          1          0     0        0   
357                 0  ...         0          1          0     0        0   
358                 0  ...         0          0          0     0        0   
359                 0  ...         0          0          0     0        0   
360                 0  ...         0          0          0     0        0   

     Redis  Join_Ignite-Sql  Join_Ignite-NoSql  Join_Virtuoso-Sql  \
0        0                0                  0                  0   
1        0                0                  0                  0   
2        0                0                  0                  0   
3        0                0                  0                  0   
4        0                0                  0                  0   
..     ...              ...                ...                ...   
356      1                0                  0                  0   
357      0                0                  0                  0   
358   

In [7]:
pd.set_option('display.max_rows', None)  # Exibir todas as linhas
pd.set_option('display.max_columns', None)  # Exibir todas as colunas
dfTeste = df10
sum_row = (dfTeste.iloc[:, :] != 0).sum(axis=0)

# Adiciona a linha de soma ao final do DataFrame com o nome 'Sum'
dfTeste.loc['Sum'] = sum_row
dfTeste

owner                               name  \
0                  Activiti                           Activiti   
1           CellularPrivacy      Android-IMSI-Catcher-Detector   
2                    Blankj                    AndroidUtilCode   
3                AntennaPod                         AntennaPod   
4           AnySoftKeyboard                    AnySoftKeyboard   
5               iBotPeaches                            Apktool   
6                asciidocfx                         AsciidocFX   
7             AxonFramework                      AxonFramework   
8             opensourceBIM                          BIMserver   
9         BroadleafCommerce                  BroadleafCommerce   
10               BuildCraft                         BuildCraft   
11                 SpigotMC                         BungeeCord   
12                  OpenHFT                      Chronicle-Map   
13                  OpenHFT                    Chronicle-Queue   
14              stanfordnlp                            CoreNLP   
15               jeremylong                    DependencyCheck   
16                 hneemann                            Digital   
17               Etar-Group                      Etar-Calendar   
18                   AlmasB                               FXGL   
19              TechEmpower                FrameworkBenchmarks   
20                 GeyserMC                             Geyser   
21          brettwooldridge                           HikariCP   
22               JSQLParser                         JSqlParser   
23                   Neamar                               KISS   
24        LawnchairLauncher                          Lawnchair   
25                  PhilJay                     MPAndroidChart   
26           MinecraftForge                     MinecraftForge   
27                     M66B                           NetGuard   
28              TeamNewPipe                            NewPipe   
29            federicoiosue                         Omni-Notes   
30          mitreid-connect  OpenID-Connect-Java-Spring-Server   
31                 LibrePDF                            OpenPDF   
32               OpenRefine                         OpenRefine   
33          opentripplanner                    OpenTripPlanner   
34           igniterealtime                           Openfire   
35                osmandapp                             OsmAnd   
36                    Col-E                              Recaf   
37            QuantumBadger                          RedReader   
38            RoaringBitmap                      RoaringBitmap   
39                ReactiveX                             RxJava   
40                  vipshop                             Saturn   
41             lukas-krecan                           ShedLock   
42                signalapp                     Signal-Android   
43           igniterealtime                              Smack   
44            SpongePowered                          SpongeAPI   
45             MovingBlocks                         Terasology   
46                  haraldk                      TwelveMonkeys   
47                Twitter4J                          Twitter4J   
48                   winder            Universal-G-Code-Sender   
49     UniversalMediaServer               UniversalMediaServer   
50                EngineHub                          WorldEdit   
51                    knowm                            XChange   
52                    knowm                             XChart   
53                   apache                           activemq   
54               real-logic                              aeron   
55                   ukanth                             afwall   
56               real-logic                             agrona   
57                   aliyun            aliyun-openapi-java-sdk   
58                  Alluxio                            alluxio   
59                   apache                             ambari

Removing projects that don't have DB clues the principal dataframe 

In [8]:
#df2 = df2.iloc[ : , 1:]
#df3[(df3 == 0).all(axis=1)].index
df2 = df2.drop(df2[(df2.iloc[ : , 8:] == 0).all(axis=1)].index)
df2

owner                               name  part_commit  \
0                  Activiti                           Activiti         1540   
1                   Alluxio                            alluxio         5886   
4           AnySoftKeyboard                    AnySoftKeyboard          703   
6                     Athou                          commafeed          465   
7                Atmosphere                         atmosphere         1326   
9             AxonFramework                      AxonFramework          630   
11        BroadleafCommerce                  BroadleafCommerce         2211   
18                FasterXML                   jackson-databind         1596   
20     GoogleContainerTools                                jib          276   
21                 Graylog2                    graylog2-server         8778   
22                    INRIA                              spoon          946   
23               JSQLParser                         JSqlParser          153   
24                   JabRef                             jabref         3741   
25               JanusGraph                         janusgraph          595   
26                JetBrains                   intellij-plugins        21115   
27                  JodaOrg                          joda-time          231   
32                     M66B                           NetGuard          630   
34               MorphiaOrg                            morphia          741   
36   NationalSecurityAgency                             ghidra         1326   
38                  Netflix                              genie          231   
39             OpenAPITools                  openapi-generator         7750   
41                  OpenHFT                    Chronicle-Queue         1225   
42               OpenRefine                         OpenRefine         1485   
43                 OpenVidu                           openvidu          780   
50               SeleniumHQ                           selenium        36315   
51              SonarSource                          sonarqube        61075   
52                 SpigotMC                         BungeeCord          171   
54                TEAMMATES                          teammates         1830   
56              TechEmpower                FrameworkBenchmarks         2211   
57                Twitter4J                          Twitter4J          171   
58     UniversalMediaServer               UniversalMediaServer         2080   
59                  VertaAI                            modeldb          561   
61                  alibaba                           fastjson          435   
62                  alibaba                              nacos          276   
63                  alibaba               spring-cloud-alibaba           55   
64                   aliyun            aliyun-openapi-java-sdk         2211   
66                   apache                           activemq         6105   
67                   apache                             ambari        17955   
68                   apache                               avro          861   
69                   apache                               beam        19900   
70                   apache                         bookkeeper          528   
71                   apache                            calcite         1540   
72                   apache                              camel       231540   
75                   apache                              drill          990   
76                   apache                              dubbo         1378   
77                   apache                              flink        52650   
78                   apache                              geode         4371   
79                   apache                            gobblin          595   
80                   apache                             groovy        17205   
81                   apache                             hadoop        29

Removing projects that don't have DB clues in the last version 

In [9]:
def select_last_commit(group):
    return group.iloc[-1]  # Seleciona o último commit

# Ordena os commits dentro de cada projeto (caso não estejam ordenados)
df_sorted = df.sort_values(by=['name', 'part_commit'])

# Aplica a função para pegar o último commit em cada grupo de projeto
df3 = df_sorted.groupby('name').apply(select_last_commit).reset_index(drop=True)

df3 = df3.drop(df3[(df3.iloc[:,8:] == 0).all(axis=1)].index) # deletando as linhas que possuem valor 0 em todas as colunas
df3

owner                               name  \
0                  Activiti                           Activiti   
1           CellularPrivacy      Android-IMSI-Catcher-Detector   
7             AxonFramework                      AxonFramework   
8             opensourceBIM                          BIMserver   
9         BroadleafCommerce                  BroadleafCommerce   
13                  OpenHFT                    Chronicle-Queue   
14              stanfordnlp                            CoreNLP   
15               jeremylong                    DependencyCheck   
19              TechEmpower                FrameworkBenchmarks   
21          brettwooldridge                           HikariCP   
22               JSQLParser                         JSqlParser   
30          mitreid-connect  OpenID-Connect-Java-Spring-Server   
32               OpenRefine                         OpenRefine   
34           igniterealtime                           Openfire   
35                osmandapp                             OsmAnd   
40                  vipshop                             Saturn   
41             lukas-krecan                           ShedLock   
42                signalapp                     Signal-Android   
49     UniversalMediaServer               UniversalMediaServer   
53                   apache                           activemq   
57                   aliyun            aliyun-openapi-java-sdk   
58                  Alluxio                            alluxio   
59                   apache                             ambari   
60                 linkedin                              ambry   
61                nextcloud                            android   
64                     line                            armeria   
66               Atmosphere                         atmosphere   
68                sleuthkit                            autopsy   
70                      aws                       aws-sdk-java   
71                      aws                    aws-sdk-java-v2   
72                  azkaban                            azkaban   
74               bazelbuild                              bazel   
76                   apache                               beam   
81                   apache                         bookkeeper   
82                 bootique                           bootique   
83               openzipkin                              brave   
84                    raphw                         byte-buddy   
85                ben-manes                           caffeine   
86                   apache                            calcite   
87                   apache                              camel   
88                  camunda               camunda-bpm-platform   
89                   apereo                                cas   
90                     cgeo                               cgeo   
91               checkstyle                         checkstyle   
95                    Athou                          commafeed   
99                    crate                              crate   
101           cuba-platform                               cuba   
102                cucumber                       cucumber-jvm   
104              iterate-ch                          cyberduck   
105                 dbeaver                            dbeaver   
106                debezium                           debezium   
108               fabric8io                docker-maven-plugin   
110                  apache                              drill   
111              dropwizard                         dropwizard   
112                  apache                              dubbo   
113               webbukkit                             dynmap   
114               ebean-orm                              ebean   
117                 ehcache                           ehcache3   
118                 elastic                      elasticsearch   
121                  google                        error-prone

Merging dataframe grouping and dataframe only last version with DB clues

In [10]:
#df3.merge(df4, on=['PROJECTS'], how='outer', suffixes=['', '_'], indicator=True)
df_mer= pd.merge(df2, df3, on= 'name', how='outer', suffixes=['', '_'], indicator=True)
df_mer

owner                               name  part_commit  \
0                  Activiti                           Activiti       1540.0   
1                   Alluxio                            alluxio       5886.0   
2           AnySoftKeyboard                    AnySoftKeyboard        703.0   
3                     Athou                          commafeed        465.0   
4                Atmosphere                         atmosphere       1326.0   
5             AxonFramework                      AxonFramework        630.0   
6         BroadleafCommerce                  BroadleafCommerce       2211.0   
7                 FasterXML                   jackson-databind       1596.0   
8      GoogleContainerTools                                jib        276.0   
9                  Graylog2                    graylog2-server       8778.0   
10                    INRIA                              spoon        946.0   
11               JSQLParser                         JSqlParser        153.0   
12                   JabRef                             jabref       3741.0   
13               JanusGraph                         janusgraph        595.0   
14                JetBrains                   intellij-plugins      21115.0   
15                  JodaOrg                          joda-time        231.0   
16                     M66B                           NetGuard        630.0   
17               MorphiaOrg                            morphia        741.0   
18   NationalSecurityAgency                             ghidra       1326.0   
19                  Netflix                              genie        231.0   
20             OpenAPITools                  openapi-generator       7750.0   
21                  OpenHFT                    Chronicle-Queue       1225.0   
22               OpenRefine                         OpenRefine       1485.0   
23                 OpenVidu                           openvidu        780.0   
24               SeleniumHQ                           selenium      36315.0   
25              SonarSource                          sonarqube      61075.0   
26                 SpigotMC                         BungeeCord        171.0   
27                TEAMMATES                          teammates       1830.0   
28              TechEmpower                FrameworkBenchmarks       2211.0   
29                Twitter4J                          Twitter4J        171.0   
30     UniversalMediaServer               UniversalMediaServer       2080.0   
31                  VertaAI                            modeldb        561.0   
32                  alibaba                           fastjson        435.0   
33                  alibaba                              nacos        276.0   
34                  alibaba               spring-cloud-alibaba         55.0   
35                   aliyun            aliyun-openapi-java-sdk       2211.0   
36                   apache                           activemq       6105.0   
37                   apache                             ambari      17955.0   
38                   apache                               avro        861.0   
39                   apache                               beam      19900.0   
40                   apache                         bookkeeper        528.0   
41                   apache                            calcite       1540.0   
42                   apache                              camel     231540.0   
43                   apache                              drill        990.0   
44                   apache                              dubbo       1378.0   
45                   apache                              flink      52650.0   
46                   apache                              geode       4371.0   
47                   apache                            gobblin        595.0   
48                   apache                             groovy      17205.0   
49                   apache                             hadoop      2989

Filtering diference in the last version

In [11]:
df5 = df_mer[(df_mer['_merge'].str.startswith('left'))]
df5

owner                  name  part_commit  isLast  SapHana  \
2    AnySoftKeyboard       AnySoftKeyboard        703.0     0.0      0.0   
15           JodaOrg             joda-time        231.0     0.0      0.0   
16              M66B              NetGuard        630.0     0.0      0.0   
26          SpigotMC            BungeeCord        171.0     0.0      0.0   
29         Twitter4J             Twitter4J        171.0     0.0      0.0   
38            apache                  avro        861.0     0.0      0.0   
58            apache                 nutch        300.0     0.0      0.0   
59            apache                   poi       7875.0     0.0      0.0   
61            apache              rocketmq        351.0     0.0      0.0   
68            apache                struts       1225.0     0.0      0.0   
73            apache             zookeeper        325.0     0.0      0.0   
75        asciidocfx            AsciidocFX         91.0     0.0      0.0   
81      bisq-network                  bisq       1431.0     0.0      0.0   
82          bitcoinj              bitcoinj       1275.0     0.0      0.0   
101    eclipse-vertx                vert.x        666.0     0.0      0.0   
104           embulk                embulk        153.0     0.0      0.0   
122      graphhopper           graphhopper       1326.0     0.0      0.0   
127          haraldk         TwelveMonkeys        120.0     0.0      0.0   
129           hcoles                pitest         91.0     0.0      0.0   
135    jMonkeyEngine         jmonkeyengine       2278.0     0.0      0.0   
139        jenkinsci               jenkins      22155.0     0.0      0.0   
144         kermitt2                grobid        153.0     0.0      0.0   
168  opentripplanner       OpenTripPlanner       2556.0     0.0      0.0   
172           oracle              opengrok       1596.0     0.0      0.0   
191      robolectric           robolectric       1770.0     0.0      0.0   
193         runelite              runelite       4560.0     0.0      0.0   
194        siddhi-io                siddhi        276.0     0.0      0.0   
201     spring-cloud  spring-cloud-netflix        231.0     0.0      0.0   
203        spring-io            initializr        190.0     0.0      0.0   
213      swagger-api          swagger-core        120.0     0.0      0.0   
223             vsch         flexmark-java        136.0     0.0      0.0   

     Realm  SAP SQL Anywhere  FileMaker  ArangoDB  Informix  HyperSQL  \
2      0.0               0.0        0.0       0.0       0.0       0.0   
15     0.0               0.0        0.0       0.0       0.0       7.0   
16     0.0               0.0        0.0       0.0       0.0       0.0   
26     0.0               0.0        0.0       0.0       0.0       0.0   
29     0.0               0.0        0.0       0.0       0.0      13.0   
38     0.0               0.0        0.0       0.0       0.0       7.0   
58     0.0               0.0        0.0       0.0       0.0       1.0   
59     0.0               0.0        0.0       0.0       0.0       2.0   
61     0.0               0.0        0.0       0.0       0.0       0.0   
68     0.0               0.0        0.0       0.0       0.0      13.0   
73     0.0               0.0        0.0       0.0       0.0       0.0   
75     0.0               0.0        0.0       0.0       0.0       0.0   
81     0.0               0.0        0.0       0.0       0.0       0.0   
82     0.0               0.0        0.0       0.0       0.0       0.0   
101    0.0               0.0        0.0       0.0       0.0       0.0   
104    0.0               0.0        0.0       0.0       0.0       0.0   
122    0.0               0.0        0.0       0.0       0.0       0.0   
127    0.0               0.0        0.0       0.0       0.0       0.0   
129    0.0               0.0        0.0       0.0       0.0       0.0   
135    0.0               0.0        0.0       0.0       0.0       0.0   
139    0.0               0.0        0.0       0.0

Merging dataframe only lines that last version projects and dataframe only lines in the last version and not DB clues

In [12]:
df_mer2= pd.merge(df10, df5.iloc[:,:2], on= 'name', how='outer', suffixes=['', '_'], indicator=True)
df_mer2

owner                               name  \
0                  Activiti                           Activiti   
1           CellularPrivacy      Android-IMSI-Catcher-Detector   
2                    Blankj                    AndroidUtilCode   
3                AntennaPod                         AntennaPod   
4           AnySoftKeyboard                    AnySoftKeyboard   
5               iBotPeaches                            Apktool   
6                asciidocfx                         AsciidocFX   
7             AxonFramework                      AxonFramework   
8             opensourceBIM                          BIMserver   
9         BroadleafCommerce                  BroadleafCommerce   
10               BuildCraft                         BuildCraft   
11                 SpigotMC                         BungeeCord   
12                  OpenHFT                      Chronicle-Map   
13                  OpenHFT                    Chronicle-Queue   
14              stanfordnlp                            CoreNLP   
15               jeremylong                    DependencyCheck   
16                 hneemann                            Digital   
17               Etar-Group                      Etar-Calendar   
18                   AlmasB                               FXGL   
19              TechEmpower                FrameworkBenchmarks   
20                 GeyserMC                             Geyser   
21          brettwooldridge                           HikariCP   
22               JSQLParser                         JSqlParser   
23                   Neamar                               KISS   
24        LawnchairLauncher                          Lawnchair   
25                  PhilJay                     MPAndroidChart   
26           MinecraftForge                     MinecraftForge   
27                     M66B                           NetGuard   
28              TeamNewPipe                            NewPipe   
29            federicoiosue                         Omni-Notes   
30          mitreid-connect  OpenID-Connect-Java-Spring-Server   
31                 LibrePDF                            OpenPDF   
32               OpenRefine                         OpenRefine   
33          opentripplanner                    OpenTripPlanner   
34           igniterealtime                           Openfire   
35                osmandapp                             OsmAnd   
36                    Col-E                              Recaf   
37            QuantumBadger                          RedReader   
38            RoaringBitmap                      RoaringBitmap   
39                ReactiveX                             RxJava   
40                  vipshop                             Saturn   
41             lukas-krecan                           ShedLock   
42                signalapp                     Signal-Android   
43           igniterealtime                              Smack   
44            SpongePowered                          SpongeAPI   
45             MovingBlocks                         Terasology   
46                  haraldk                      TwelveMonkeys   
47                Twitter4J                          Twitter4J   
48                   winder            Universal-G-Code-Sender   
49     UniversalMediaServer               UniversalMediaServer   
50                EngineHub                          WorldEdit   
51                    knowm                            XChange   
52                    knowm                             XChart   
53                   apache                           activemq   
54               real-logic                              aeron   
55                   ukanth                             afwall   
56               real-logic                             agrona   
57                   aliyun            aliyun-openapi-java-sdk   
58                  Alluxio                            alluxio   
59                   apache                             ambari

Filtering only lines in the last version and not DB clues

In [13]:
df6 = df_mer2[(df_mer2['_merge'].str.startswith('bo'))]
df6

owner                  name                     domain  \
4    AnySoftKeyboard       AnySoftKeyboard                      Other   
6         asciidocfx            AsciidocFX                      Media   
11          SpigotMC            BungeeCord                       Game   
27              M66B              NetGuard                   Security   
33   opentripplanner       OpenTripPlanner            Data Management   
46           haraldk         TwelveMonkeys                      Media   
47         Twitter4J             Twitter4J                      Media   
69            apache                  avro            Data Management   
77      bisq-network                  bisq             Cryptocurrency   
79          bitcoinj              bitcoinj             Cryptocurrency   
120           embulk                embulk            Data Management   
126             vsch         flexmark-java       Software Development   
151      graphhopper           graphhopper            Data Management   
154         kermitt2                grobid   Artificial Intelligence    
170        spring-io            initializr       Software Development   
189        jenkinsci               jenkins                 Automation   
193    jMonkeyEngine         jmonkeyengine                       Game   
195          JodaOrg             joda-time       Software Development   
251           apache                 nutch            Data Management   
256           oracle              opengrok           Program Analysis   
267           hcoles                pitest           Program Analysis   
269           apache                   poi       Software Development   
287      robolectric           robolectric           Program Analysis   
288           apache              rocketmq            Data Management   
290         runelite              runelite                       Game   
301        siddhi-io                siddhi            Data Management   
319     spring-cloud  spring-cloud-netflix  Infrastructure Management   
328           apache                struts       Software Development   
329      swagger-api          swagger-core       Software Development   
348    eclipse-vertx                vert.x  Infrastructure Management   
358           apache             zookeeper  Infrastructure Management   

                                         sha1  part_commit  \
4    2fc649dc3398b1c762a85a803a43ce814519665b           37   
6    1c9442bafbb505446e7548307d3908e8ec123f7e           13   
11   c3f228f626af6da1dc126e7f96062cfc44d5b10f           18   
27   132e4c8d4e78194d682f2141a4579bde65c7cb2e           35   
33   178ebec96bbb2d611f5b2f62979bcb1a29d4b716           71   
46   dd174c7f7ee167930afca01770b9bba84846a3aa           15   
47   9d705c33235b7358d2161bd03c7760fbc6919532           18   
69   2d3029ddae1ade2769bcb8b30e597db25dd56d1f           41   
77   fcb625cbb430a06736c87948a56554dc3f080add           53   
79   0080f79a051bf47dda1b62927dee2160cf6cba34           50   
120  2325334d01f6930fd03964dfc2d0975cb57943ab           17   
126  b474894c84e29562e25e20705e7dc895e6319177           16   
151  ef73fd72100ebdd6dfad70b41730f0f8b8c7f996           51   
154  69728c6bafb57e35aee39f3b8f57311bc94a6349           17   
170  ce987280aad0b287b5411930604c9c096484f26e           19   
189  8458d66713fc400113d08804c0a6ff4ee9212114          210   
193  3618ff0f1849d56d57f1f2869e16789de38b5ad6           67   
195  8286fb0c8004ba27491ba8bd6647a2fb3e3b2067           21   
251  8fc4f17acc5da28c22ef4e77c2316e20e5976f02           24   
256  e264dd9045f3e7e9e77bdf2b80708c8c50f5d00e           56   
267  61fff8e91fd3ff3339f97765435b74254616e49d           13   
269  3d1375deee56ea921c35e86bcb8fe3e511fb80aa          125   
287  385af9f0ff985d61742ee6a2a635c3db7488156f           59   
288  d3e5f70979f74349db9c5ebbe3b48ff59b52d677           26   
290  db484aceb95e8520f5e15c7cbddb590fb18e7ff3           95   
301  1e160212554bf01fb4775d245c4defcca1247a02           23   
319 

Concatening dataframes

In [14]:
df_concat2 =  pd.concat([df3, df6]).drop_duplicates()
df_concat2

owner                               name  \
0                  Activiti                           Activiti   
1           CellularPrivacy      Android-IMSI-Catcher-Detector   
7             AxonFramework                      AxonFramework   
8             opensourceBIM                          BIMserver   
9         BroadleafCommerce                  BroadleafCommerce   
13                  OpenHFT                    Chronicle-Queue   
14              stanfordnlp                            CoreNLP   
15               jeremylong                    DependencyCheck   
19              TechEmpower                FrameworkBenchmarks   
21          brettwooldridge                           HikariCP   
22               JSQLParser                         JSqlParser   
30          mitreid-connect  OpenID-Connect-Java-Spring-Server   
32               OpenRefine                         OpenRefine   
34           igniterealtime                           Openfire   
35                osmandapp                             OsmAnd   
40                  vipshop                             Saturn   
41             lukas-krecan                           ShedLock   
42                signalapp                     Signal-Android   
49     UniversalMediaServer               UniversalMediaServer   
53                   apache                           activemq   
57                   aliyun            aliyun-openapi-java-sdk   
58                  Alluxio                            alluxio   
59                   apache                             ambari   
60                 linkedin                              ambry   
61                nextcloud                            android   
64                     line                            armeria   
66               Atmosphere                         atmosphere   
68                sleuthkit                            autopsy   
70                      aws                       aws-sdk-java   
71                      aws                    aws-sdk-java-v2   
72                  azkaban                            azkaban   
74               bazelbuild                              bazel   
76                   apache                               beam   
81                   apache                         bookkeeper   
82                 bootique                           bootique   
83               openzipkin                              brave   
84                    raphw                         byte-buddy   
85                ben-manes                           caffeine   
86                   apache                            calcite   
87                   apache                              camel   
88                  camunda               camunda-bpm-platform   
89                   apereo                                cas   
90                     cgeo                               cgeo   
91               checkstyle                         checkstyle   
95                    Athou                          commafeed   
99                    crate                              crate   
101           cuba-platform                               cuba   
102                cucumber                       cucumber-jvm   
104              iterate-ch                          cyberduck   
105                 dbeaver                            dbeaver   
106                debezium                           debezium   
108               fabric8io                docker-maven-plugin   
110                  apache                              drill   
111              dropwizard                         dropwizard   
112                  apache                              dubbo   
113               webbukkit                             dynmap   
114               ebean-orm                              ebean   
117                 ehcache                           ehcache3   
118                 elastic                      elasticsearch   
121                  google                        error-prone

In [15]:
#df3 = df3.iloc[ : , 2:] #desconiderandcoluna commits 
#df3[(df3 == 0).all(axis=1) # filtra as linhas que possuem valor igual a 0 em todas as colunas


In [16]:
#df2 = df2.astype(np.uint8)

In [17]:
df_concat2.drop(["owner","name", "domain", "sha1", "part_commit", "date_commit", "isLast", "owner_", "_merge"], axis=1, inplace=True)
df_concat2

SapHana  Realm  SAP SQL Anywhere  FileMaker  ArangoDB  Informix  \
0          0      0                 0          0         0         0   
1          0      1                 0          0         0         0   
7          0      0                 0          0         0         0   
8          0      0                 0          0         0         0   
9          0      0                 0          0         0         0   
13         0      0                 0          0         0         0   
14         0      0                 0          0         0         0   
15         0      0                 0          0         0         0   
19         0      0                 0          0         0         0   
21         0      0                 0          0         0         0   
22         0      0                 0          0         0         0   
30         0      0                 0          0         0         0   
32         0      0                 0          0         0         0   
34         0      0                 0          0         0         0   
35         0      0                 0          0         0         0   
40         0      0                 0          0         0         0   
41         0      0                 0          0         1         0   
42         0      0                 0          0         0         0   
49         0      0                 0          0         0         0   
53         0      0                 0          0         0         0   
57         0      0                 0          0         0         0   
58         0      0                 0          0         0         0   
59         0      0                 1          0         0         0   
60         0      0                 0          0         0         0   
61         0      0                 0          0         0         0   
64         0      0                 0          0         0         0   
66         0      0                 0          0         0         0   
68         0      0                 0          0         0         0   
70         0      0                 0          0         0         0   
71         0      0                 0          0         0         0   
72         0      0                 0          0         0         0   
74         0      0                 0          0         0         0   
76         0      0                 0          0         0         0   
81         0      0                 0          0         0         0   
82         0      0                 0          0         0         0   
83         0      0                 0          0         0         0   
84         0      0                 0          0         0         0   
85         0      0                 0          0         0         0   
86         0      0                 0          0         0         0   
87         0      0                 0          0         1         0   
88         0      0                 0          0         0         0   
89         0      0                 0          0         0         0   
90         0      0                 0          0         0         0   
91         0      0                 0          0         0         0   
95         0      0                 0          0         0         0   
99         0      0                 0          0         0         0   
101        0      0                 0          0         0         0   
102        0      0                 0          0         0         0   
104        0      0                 0          0         0         0   
105        1      0                 0          0         0         1   
106        0      0                 0          0         0         0   
108        0      0                 0          0         0         0   
110        0      0                 0          0         0         0   
111        0      0                 0          0         0         0   
112        0      0                 0        

ASSOCIATION RULES

In [18]:
frq_items = apriori(df_concat2, min_support = 0.021, use_colnames = True)

In [19]:
rules = association_rules(frq_items, metric ="lift", min_threshold = 1)

In [20]:
# Sorting the rules by the lift measure 
rules = rules.sort_values('lift', ascending =False)
print(rules.head())

                                              antecedents  \
194476                  (SQLite, H2, SAP Adaptive Server)   
366862           (MySQL, SQLite, H2, SAP Adaptive Server)   
291861      (MySQL, SQLite, IBM DB2, SAP Adaptive Server)   
342714  (HyperSQL, MS SQL Server, IBM DB2, PostgreSQL,...   
342735  (Oracle, MS SQL Server, IBM DB2, PostgreSQL, I...   

                                              consequents  antecedent support  \
194476        (Firebird, Oracle, Informix, MS SQL Server)            0.021645   
366862  (Oracle, MS SQL Server, IBM DB2, PostgreSQL, I...            0.021645   
291861        (Firebird, Oracle, Informix, MS SQL Server)            0.021645   
342714              (Oracle, SQLite, SAP Adaptive Server)            0.025974   
342735            (HyperSQL, SQLite, SAP Adaptive Server)            0.025974   

        consequent support   support  confidence  lift  leverage  conviction  
194476            0.025974  0.021645    1.000000  38.5  0.021083   

In [ ]:
rules

In [ ]:
rules['antecedent_len'] = rules['antecedents'].apply(lambda x: len(x))
rules['consequente_len'] = rules['consequents'].apply(lambda x: len(x))

Filtering only the rules of size 2, that is, 1 antecedent and 1 consequent. 

In [ ]:
rules_filter = rules[(rules['antecedent_len'] == 1) & (rules['consequente_len'] == 1)]

Showing all filtered rules.

In [ ]:
rules_filter

antecedents            consequents  antecedent support  \
404               (Ingres)             (Firebird)            0.021645   
405             (Firebird)               (Ingres)            0.047619   
67              (Informix)            (MS Access)            0.043290   
66             (MS Access)             (Informix)            0.030303   
50   (SAP Adaptive Server)     (SAP SQL Anywhere)            0.060606   
..                     ...                    ...                 ...   
226                   (H2)             (DynamoDB)            0.389610   
55                 (Redis)     (SAP SQL Anywhere)            0.350649   
54      (SAP SQL Anywhere)                (Redis)            0.064935   
489                (Redis)  (SAP Adaptive Server)            0.350649   
488  (SAP Adaptive Server)                (Redis)            0.060606   

     consequent support   support  confidence       lift  leverage  \
404            0.047619  0.021645    1.000000  21.000000  0.020614   
405            0.021645  0.021645    0.454545  21.000000  0.020614   
67             0.030303  0.021645    0.500000  16.500000  0.020333   
66             0.043290  0.021645    0.714286  16.500000  0.020333   
50             0.064935  0.060606    1.000000  15.400000  0.056671   
..                  ...       ...         ...        ...       ...   
226            0.125541  0.056277    0.144444   1.150575  0.007365   
55             0.064935  0.025974    0.074074   1.140741  0.003205   
54             0.350649  0.025974    0.400000   1.140741  0.003205   
489            0.060606  0.021645    0.061728   1.018519  0.000394   
488            0.350649  0.021645    0.357143   1.018519  0.000394   

     conviction  antecedent_len  consequente_len  
404         inf               1                1  
405    1.793651               1                1  
67     1.939394               1                1  
66     3.348485               1                1  
50          inf               1                1  
..          ...             ...              ...  
226    1.022095               1                1  
55     1.009870               1                1  
54     1.082251               1                1  
489    1.001196               1                1  
488    1.010101               1                1  

[508 rows x 11 columns]

In [ ]:
HISTORICAL_RULES_FILE = RESOURCE_DIR + os.sep + 'historical_rulesv10.xlsx'    #'seq_patterns/testes/historical_rules_commit10_197reg_021.xlsx'
rules_filter = rules_filter.to_excel(HISTORICAL_RULES_FILE, index=False)